In [98]:
#put your own path for input and save files. Mandatory!
dir <- file.path("/Users/ghoareau/Documents/Guilhem/UPPA/Projets-UPPA/2016-Datation-U-Pb-calcite/test-iolite")

In [100]:
#Tera-Wasserburg ou Wetherill? Put the right answer
diagram <- 'TW' #'TW' or 'Weth'

In [101]:
format <- 2
if (diagram == 'Weth') {format = 1
}else {format = 2}

## Multi-age calculation

### Table generation

In [80]:
#Function for significant digits
dfDigits <- function(x, digits = 4) {
    ## x is a data.frame
    for (col in colnames(x)[sapply(x, class) == 'numeric'])
        x[,col] <- round(x[,col], digits = digits)
    x
}

#Call library
library(IsoplotR)

#Settings for fixed Pb0 (! Does not work)
settings('iratio','Pb207Pb206',0.85)

#Call input file
if (format == 1) {Dataset0 <- read.table(file.path(dir,"moy_ste_spot_wetherill.txt"),sep='\t')
}else {Dataset0 <- read.table(file.path(dir,"moy_ste_spot_TW.txt"),sep='\t')}

#Build table
df1 = as.data.frame(matrix(ncol=6, nrow=0))
colnames(df1)<-c('age','err_age','Pb0','err_Pb0','mswd','n')

#Loop for age calculation. See IsoplotR documentation for details
for (i in 1:nrow(unique(Dataset0[c(1,2)]))) {
    Dataset0_new <- Dataset0[Dataset0$V1 == unique(Dataset0[c(1,2)])[i,1]&Dataset0$V2 == unique(Dataset0[c(1,2)])[i,2], ]
    dat1 <- read.data(Dataset0_new[c(3:6,7)],method='U-Pb',format=format,ierr=2)
    age <- age(isochron = TRUE,dat1,type = 3,exterr = TRUE,sigdig = 5)
    df1[i,1] <- age$par['t']
    df1[i,3] <- age$par['a0']
    ci_age <- ci(x=age$par['t'],sx=age$err[,'t'],oerr = 3,df=age$df)
    ci_Pb0 <- ci(x=age$par['a0'],sx=age$err[,'a0'],oerr = 3,df=age$df)
    if (is.na(ci_age['disp'])){
        df1[i,2] <- ci_age
        df1[i,4] <- ci_Pb0
    }else{
        df1[i,2] <- ci_age['disp']
        df1[i,4] <- ci_Pb0['disp']
        }
    df1[i,5] <- age$mswd
    df1[i,6] <- nrow(Dataset0_new)
    }
df1 <- df1[order(df1$err_age, df1$mswd, decreasing = FALSE),]
df1 <- dfDigits(df1, 4)

#Save csv table
if (format == 1) {write.csv(df1,file.path(dir,"multiage_wetherill.csv"), row.names = FALSE)
}else {write.csv(df1,file.path(dir,"multiage_TW.csv"), row.names = FALSE)}
                            
df1

age     err_age Pb0    err_Pb0 mswd   n 
1 62.0983 0.8689  0.7281 0.0107  7.0023 60

### Plot generation

In [84]:
i = 1
#Call library
library(IsoplotR)

#Settings for fixed Pb0 (for TW)
settings('iratio','Pb207Pb206',0.85,0)

#Call input file + pdf creation
if (format == 1) {Dataset0 <- read.table(file.path(dir,"moy_ste_spot_wetherill.txt"),sep='\t')
                  pdf(file = file.path(dir,"multiplot_Wetherill.pdf"))
                  type = 1
}else {Dataset0 <- read.table(file.path(dir,"moy_ste_spot_TW.txt"),sep='\t')
       pdf(file = file.path(dir,"multiplot_TW.pdf"))
       type = 2
}

par(mfrow=c(1,1))

#Loop for age calculation. See IsoplotR documentation for details
for (i in 1:nrow(unique(Dataset0[c(1,2)]))) {
    Dataset0_new <- Dataset0[Dataset0$V1 == unique(Dataset0[c(1,2)])[i,1]&Dataset0$V2 == unique(Dataset0[c(1,2)])[i,2], ]
    dat1 <- read.data(Dataset0_new[c(3:6,7)],method='U-Pb',format=format,ierr=2)#11
    concordia_ <- concordia(dat1,type=type,show.age=2,exterr=TRUE,oerr=3,sigdig = 3,ellipse.fill=NA,ticks=0)#,anchor=1)#,ellipse.stroke=NA))
    }
dev.off()

pdf 
  2

## Age calculation from sub-images

### Table generation

In [88]:
#Attention The size of the virtual spots defined in Iolite must be the same size as the sub-image virtual spots used here
#Example: for 200 µm x 200 µm sub-image with 25 µm x 25 µm virtual spots, a unique grid with 25 µm x 25 µm must be created with Iolite

#Function for significant digits
dfDigits <- function(x, digits = 4) {
    ## x is a data.frame
    for (col in colnames(x)[sapply(x, class) == 'numeric'])
        x[,col] <- round(x[,col], digits = digits)
    x
}

#Call library
library(IsoplotR)

#Size of sub-image: h1 = horizontal length, l1 = vertical length in µm
h1 <- 400
l1 <- 400

#Size of virtual spots in each sub-image: hps1 = horizontal length, lps1 = vertical length in µm
hps1 <- 100
lps1 <- 100

#Call input file
if (format == 1) {Dataset0 <- read.table(file.path(dir,"moy_ste_spot_wetherill.txt"),sep='\t')
}else {Dataset0 <- read.table(file.path(dir,"moy_ste_spot_TW.txt"),sep='\t')}

#Other variables
n <- (h1*l1)/(hps1*lps1)    #number of virtual spots per sub-image
n <- as.integer(n)
nb_subset <- as.integer(nrow(Dataset0)/n)    #number of sub-images
nb_lines <- nb_subset*n    #noumber of lines to keep from input file

#Dataset0 modification to remove any supernumerary lines
Dataset0 <- Dataset0[1:nb_lines, ]

#Add a column with a number for each number of sub-images
seq <- rep(1:nb_subset, each=n)
Dataset1 <- cbind(Dataset0, seq)

#Create result table with headere
df1 = as.data.frame(matrix(ncol=6, nrow=0))
colnames(df1)<-c('age','err_age','Pb0','err_Pb0','mswd','n')

#Loop for age calculation. See IsoplotR documentation for details
for (i in unique(seq)) {
    Dataset1_new <- Dataset1[Dataset1$seq == i, ]    #selection of subsets with nrow = n
    dat1 <- read.data(Dataset1_new[c(3:6,7)],method='U-Pb',format=format,ierr=2)    #class UPb
    age <- age(dat1,type = 3,exterr = TRUE,sigdig = 5)   #calculation age
    df1[i,1] <- age$par['t']
    df1[i,3] <- age$par['a0']
    ci_age <- ci(x=age$par['t'],sx=age$err[,'t'],oerr = 3,df=age$df)
    ci_Pb0 <- ci(x=age$par['a0'],sx=age$err[,'a0'],oerr = 3,df=age$df)
    if (is.na(ci_age['disp'])){
        df1[i,2] <- ci_age
        df1[i,4] <- ci_Pb0
    }else{
        df1[i,2] <- ci_age['disp']
        df1[i,4] <- ci_Pb0['disp']
        }
    df1[i,5] <- age$mswd
    df1[i,6] <- nrow(Dataset1_new)
    }
df1 <- df1[order(df1$err_age, df1$mswd, decreasing = FALSE),]
df1 <- dfDigits(df1, 4)

#Save csv table
if (format == 1) {write.csv(df1,file.path(dir,"Multiage_subimage_wetherill.csv"), row.names = FALSE)
}else {write.csv(df1,file.path(dir,"Multiage_subimage_TW.csv"), row.names = FALSE)}
df1

age     err_age Pb0    err_Pb0 mswd   n 
3 63.9178 0.8589  0.7452 0.0089  1.5727 16
1 62.5807 1.1527  0.7595 0.0258  3.9872 16
2 62.7877 1.4017  0.7333 0.0210  6.3258 16

### Plot generation

In [89]:
#Attention The size of the virtual spots defined in Iolite must be the same size as the sub-image virtual spots used here
#Example: for 200 µm x 200 µm sub-image with 25 µm x 25 µm virtual spots, a unique grid with 25 µm x 25 µm must be created with Iolite

#Function for significant digits
dfDigits <- function(x, digits = 4) {
    ## x is a data.frame
    for (col in colnames(x)[sapply(x, class) == 'numeric'])
        x[,col] <- round(x[,col], digits = digits)
    x
}

#Call library
library(IsoplotR)

#Size of sub-image: h1 = horizontal length, l1 = vertical length in µm
h1 <- 400
l1 <- 400

#Size of virtual spots in each sub-image: hps1 = horizontal length, lps1 = vertical length in µm
hps1 <- 100
lps1 <- 100

#Call input file + pdf creation
if (format == 1) {Dataset0 <- read.table(file.path(dir,"moy_ste_spot_wetherill.txt"),sep='\t')
                  pdf(file = file.path(dir,"Multiage_subimage_Wetherill.pdf"))
                  type = 1
}else {Dataset0 <- read.table(file.path(dir,"moy_ste_spot_TW.txt"),sep='\t')
       pdf(file = file.path(dir,"Multiage_subimage_TW.pdf"))
       type = 2
}

par(mfrow=c(1,1))

#Other variables
n <- (h1*l1)/(hps1*lps1)    #number of virtual spots per sub-image
n <- as.integer(n)
nb_subset <- as.integer(nrow(Dataset0)/n)    #number of sub-images
nb_lines <- nb_subset*n    #noumber of lines to keep from input file

#Dataset0 modification to remove any supernumerary lines
Dataset0 <- Dataset0[1:nb_lines, ]

#Add a column with a number for each number of sub-images
seq <- rep(1:nb_subset, each=n)
Dataset1 <- cbind(Dataset0, seq)

#Loop for age calculation. See IsoplotR documentation for details
for (i in unique(seq)) {
    Dataset1_new <- Dataset1[Dataset1$seq == i, ]
    dat1 <- read.data(Dataset1_new[c(3:6,7)],method='U-Pb',format=format,ierr=2)
    concordia_ <- concordia(dat1,type=type,show.age=2,sigdig = 3,ellipse.fill=NA,ticks=0)
    }
dev.off()

pdf 
  2

## Age calculation from 'Rectis' method

In [103]:
#Call library
library(IsoplotR)

#Settings for fixed Pb0
settings('iratio','Pb207Pb206',0.74)

#Call input file

#Call input file + pdf creation
if (format == 1) {Dataset0 <- read.table(file.path(dir,"moy_ste_spot_ODR_Rectis_Wetherill.txt"),sep='\t')
                  pdf(file = file.path(dir,"plot_cpsat_weth.pdf"))
                  type = 1
}else {Dataset0 <- read.table(file.path(dir,"moy_ste_spot_ODR_Rectis_TW.txt"),sep='\t')
       pdf(file = file.path(dir,"plot_cpsat_TW.pdf"))
       type = 2
}

#Age calcution and plot generation. See IsoplotR for details.
dat1 <- read.data(Dataset0[c(3:6,7)],method='U-Pb',format=format,ierr=2)
concordia_ <- concordia(dat1,type=type,show.age=2,exterr=TRUE,oerr=3,sigdig = 3,ellipse.fill=NA,ticks=0)#,anchor=1)#,ellipse.stroke=NA))
dev.off()

pdf 
  2